In [1]:
import random
import nltk
import re
import numpy as np
import pandas as pd
from nltk.util import ngrams
from collections import defaultdict, Counter
nltk.download('punkt')
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset # для создания датасета
from sklearn.metrics import f1_score
from torch.nn.utils.rnn import pad_sequence
import time

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
def clean_text(text):
  text = re.sub(r'[^\w]', ' ', text).lower()
  text = re.sub(r'[0-9]', ' ', text)
  text = re.sub(r'[- _]', ' ',text)

  return text

### Задание 1.

Найти в открытом доступе датасет со стихотворным текстом.

Осуществить генерацию текста на основе цепей Маркова. Рассмотреть примеры по различным n-граммам.

In [3]:
# Читаем текст из файла
with open("/content/karenina.txt", 'r', encoding='utf-8') as f:
    text = f.read()

text

'\nВсе счастливые семьи похожи друг на друга, каждая несчастливая семья несчастлива по-своему.\n\nВсе смешалось в доме Облонских. Жена узнала, что муж был в связи с бывшею в их доме француженкою-гувернанткой, и объявила мужу, что не может жить с ним в одном доме. Положение это продолжалось уже третий день и мучительно чувствовалось и самими супругами, и всеми членами семьи, и домочадцами. Все члены семьи и домочадцы чувствовали, что нет смысла в их сожительстве и что на каждом постоялом дворе случайно сошедшиеся люди более связаны между собой, чем они, члены семьи и домочадцы Облонских. Жена не выходила из своих комнат, мужа третий день не было дома. Дети бегали по всему дому, как потерянные; англичанка поссорилась с экономкой и написала записку приятельнице, прося приискать ей новое место; повар ушел еще вчера со двора, во время самого обеда; черная кухарка и кучер просили расчета.\n\nНа третий день после ссоры князь Степан Аркадьич Облонский – Стива, как его звали в свете, – в обычны

In [6]:
text = re.sub(r'[^\w\s]', '', text).lower()
tokens = text.split()

In [7]:
# подсчет количества слов
frequency_dict = Counter(tokens)
frequency_dict = dict(frequency_dict)
print(frequency_dict)

{'все': 1684, 'счастливые': 3, 'семьи': 15, 'похожи': 5, 'друг': 88, 'на': 3676, 'друга': 56, 'каждая': 10, 'несчастливая': 1, 'семья': 9, 'несчастлива': 10, 'посвоему': 9, 'смешалось': 5, 'в': 6112, 'доме': 50, 'облонских': 7, 'жена': 93, 'узнала': 32, 'что': 5825, 'муж': 87, 'был': 931, 'связи': 31, 'с': 3470, 'бывшею': 1, 'их': 436, 'француженкоюгувернанткой': 1, 'и': 13189, 'объявила': 9, 'мужу': 62, 'не': 6612, 'может': 399, 'жить': 101, 'ним': 355, 'одном': 41, 'положение': 140, 'это': 2274, 'продолжалось': 15, 'уже': 602, 'третий': 32, 'день': 175, 'мучительно': 31, 'чувствовалось': 5, 'самими': 1, 'супругами': 2, 'всеми': 60, 'членами': 2, 'домочадцами': 1, 'члены': 12, 'домочадцы': 2, 'чувствовали': 12, 'нет': 600, 'смысла': 13, 'сожительстве': 1, 'каждом': 22, 'постоялом': 2, 'дворе': 14, 'случайно': 9, 'сошедшиеся': 3, 'люди': 97, 'более': 270, 'связаны': 6, 'между': 192, 'собой': 124, 'чем': 421, 'они': 650, 'выходила': 7, 'из': 773, 'своих': 120, 'комнат': 6, 'мужа': 135, 

In [9]:
n_grams = defaultdict(list)
def generate_text(n, length):
  # Создание n-грамм
  for i in range(len(tokens) - n):
      n_gram = tuple(tokens[i:i+n])
      n_grams[n_gram[:-1]].append(n_gram[-1])

  current_gram = random.choice(list(n_grams.keys()))
  generated_text = list(current_gram)

  for _ in range(length - n + 1):  # Генерация заданной длины
      next_words = n_grams[current_gram]
      if not next_words:
          break  # Если нет следующих слов, прерываем
      next_word = random.choice(next_words)
      generated_text.append(next_word)
      current_gram = current_gram[1:] + (next_word,)  # Обновление текущего n-грамма
  print(generated_text[0])

  return ' '.join(generated_text)

In [10]:
# Эксперименты с разными n
for n in range(1, 6):  # Пробуем n от 1 до 5
    print(f"Сгенерированный текст для n={n}:")
    print(generate_text(n, length=50))
    print("\n" + "=" * 100 + "\n")

Сгенерированный текст для n=1:
скучать
скучать


Сгенерированный текст для n=2:
наблюдения
наблюдения над своим привычным ей и кончилось тем более всего этого же глядя не может высоко на ступеньках левин видел что те ее лицо его внешностью среднего роста плотный с тою особенною улыбкой изгибавшею ее маленькую худенькую и твердые мнения чтоб увидать вронского из двери и вновь покрытой бумажкой с


Сгенерированный текст для n=3:
высоком
высоком куполе каждый раз высовывалась чьянибудь лошадь и поехал в присутствие облонского и туровцына с ним на ты со всеми но видал каждый день приходят к следующим физических недостатков нет как кити способна была в молодости в описании семьи щербацких есть и он любил и на возносящуюся желтояркую звезду в


Сгенерированный текст для n=4:
чтобы
чтобы сделать как я хотела нет как ты хотел так и делай как велено крикнул левин садясь на катки пошел собак держи филипп левин испытывал теперь оставив позади себя все заботы семейные и хозяйственные такое сильное

### Задание 2

Загрузите текст из произведений Ницше ('nietzsche.txt', origin='https://s3.amazonaws.com/text-datasets/nietzsche.txt'). С помощью RNN, LSTM, GPU произведите генерацию текста.

In [ ]:
# Читаем текст из файла
with open("/content/nietzsche.txt", 'r', encoding='utf-8') as f:
    text_nth = f.read()

In [ ]:
text_nth = clean_text(text_nth)

In [ ]:
# Кодировка символов числами:

# Объединяем все предложения вместе и извлекаем уникальные символы из объединенных предложений
chars = set(''.join(text_nth) + ' ')

# Создание словаря, который сопоставляет целые числа с символами
ind_to_char = dict(enumerate(chars))

# Создание другого словаря, который сопоставляет символы с целыми числами
char_to_ind = {char: ind for ind, char in ind_to_char.items()}

In [ ]:
# Подготовка входных и выходных последовательностей:

input_seq = []  # исходная последовательность
target_seq = []  # последовательность, смещенная на 1 (без первого символа)

for i in range(len(text_nth)):
    # Удаляем последний символ для исходной последовательности
    input_seq.append(text_nth[i][:-1])

    # Удаляем первый символ для выходной последовательности
    target_seq.append(text_nth[i][1:])

    print("Исходная последовательность: {}\nЦелевая последовательность: {}".format(input_seq[i], target_seq[i]))

Выходные данные были обрезаны до нескольких последних строк (5000).
Исходная последовательность: u
Целевая последовательность: p
Исходная последовательность: on
Целевая последовательность: ne
Исходная последовательность: 
Целевая последовательность: 
Исходная последовательность: ow
Целевая последовательность: wn
Исходная последовательность: wil
Целевая последовательность: ill
Исходная последовательность: onc
Целевая последовательность: nce
Исходная последовательность: fo
Целевая последовательность: or
Исходная последовательность: al
Целевая последовательность: ll
Исходная последовательность: an
Целевая последовательность: nd
Исходная последовательность: thi
Целевая последовательность: his
Исходная последовательность: i
Целевая последовательность: s
Исходная последовательность: easie
Целевая последовательность: asier
Исходная последовательность: tha
Целевая последовательность: han
Исходная последовательность: t
Целевая последовательность: o
Исходная последовательность: giv
Целевая после

In [ ]:
input_seq_indices = []
target_seq_indices = []

for seq in input_seq:
    indices = [char_to_ind[char] for char in seq if char in char_to_ind]
    if indices:  # добавляем только непустые последовательности
        input_seq_indices.append(indices)

for seq in target_seq:
  indices = [char_to_ind[char] for char in seq if char in char_to_ind]
  if indices:
        target_seq_indices.append(indices)

# Проверка, если есть пустые последовательности
if not input_seq_indices:
    raise ValueError("Все последовательности пустые. Проверьте входные данные.")

if not target_seq_indices:
    raise ValueError("Все последовательности пустые. Проверьте выходные данные.")

In [ ]:
# Преобразуем в тензоры
X = torch.nn.utils.rnn.pad_sequence([torch.tensor(seq, dtype=torch.long) for seq in input_seq_indices], batch_first=True)
y = torch.tensor([seq[-1] for seq in target_seq_indices], dtype=torch.long).view(-1, 1)

# Проверка размеров
print("Размер X:", X.size())
print("Размер y:", y.size())

Размер X: torch.Size([98526, 19])
Размер y: torch.Size([98526, 1])


#### LSTM

In [146]:
class LSTMModel(nn.Module):
    def __init__(self, input_size, embedding_dim, hidden_size, output_size):
        super(LSTMModel, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(num_embeddings=input_size, embedding_dim=input_size)

        # Определение LSTM слоя
        self.lstm = nn.LSTM(input_size, hidden_size, batch_first=True)

        # Полносвязный слой для перехода от скрытого состояния к выходу
        self.fc = nn.Linear(hidden_size, output_size)

    def forward(self, x):
      x = self.embedding(x)  # x теперь имеет размер [batch_size, seq_length, embedding_dim]

      # Прямой проход через LSTM
      out, (hn, cn) = self.lstm(x)  # out имеет размер [batch_size, seq_length, hidden_size]


      # Получаем последний временной шаг
      out = out[:, -1, :]  # Теперь out имеет размер [batch_size, hidden_size]

      # Применяем полносвязный слой
      out = self.fc(out)


      return out

In [ ]:
input_size = len(chars)
embedding_dim = 128
hidden_size = 256
output_size = len(chars)


# Предположим, что вы уже создали экземпляр вашей модели
model = LSTMModel(input_size,embedding_dim,  hidden_size, output_size)


# Определение функции потерь и оптимизатора
criterion = nn.CrossEntropyLoss()  # Для многоклассовой классификации
optimizer = optim.Adam(model.parameters(), lr=0.001)

In [ ]:
# Создание TensorDataset
dataset = TensorDataset(X, y)

# Создание DataLoader
dataloader = DataLoader(dataset, batch_size=128)

In [ ]:
len(chars)

28

In [ ]:
# Пример цикла обучения
num_epochs = 50
for epoch in range(num_epochs):
    model.train()
    for batch_X, batch_y in dataloader:
        optimizer.zero_grad()
        outputs = model(batch_X)

        batch_y = batch_y.view(-1)

        loss = criterion(outputs, batch_y)
        loss.backward()
        optimizer.step()

    print(f'Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}')

Epoch [1/50], Loss: 0.9112
Epoch [2/50], Loss: 0.5135
Epoch [3/50], Loss: 0.4351
Epoch [4/50], Loss: 0.3339
Epoch [5/50], Loss: 0.2571
Epoch [6/50], Loss: 0.2291
Epoch [7/50], Loss: 0.2305
Epoch [8/50], Loss: 0.2622
Epoch [9/50], Loss: 0.2603
Epoch [10/50], Loss: 0.2064
Epoch [11/50], Loss: 0.2078
Epoch [12/50], Loss: 0.1864
Epoch [13/50], Loss: 0.2207
Epoch [14/50], Loss: 0.1835
Epoch [15/50], Loss: 0.1861
Epoch [16/50], Loss: 0.1783
Epoch [17/50], Loss: 0.1793
Epoch [18/50], Loss: 0.1864
Epoch [19/50], Loss: 0.2239
Epoch [20/50], Loss: 0.1864
Epoch [21/50], Loss: 0.1702
Epoch [22/50], Loss: 0.1794
Epoch [23/50], Loss: 0.1765
Epoch [24/50], Loss: 0.1730
Epoch [25/50], Loss: 0.1673
Epoch [26/50], Loss: 0.1742
Epoch [27/50], Loss: 0.1715
Epoch [28/50], Loss: 0.1911
Epoch [29/50], Loss: 0.1665
Epoch [30/50], Loss: 0.1685
Epoch [31/50], Loss: 0.1686
Epoch [32/50], Loss: 0.1673
Epoch [33/50], Loss: 0.1675
Epoch [34/50], Loss: 0.1662
Epoch [35/50], Loss: 0.1722
Epoch [36/50], Loss: 0.1688
E

In [ ]:
model.eval()  # Переключаем модель в режим оценки
all_preds = []
all_labels = []
with torch.no_grad():
    for batch_X, batch_y in dataloader:
        outputs = model(batch_X)
        _, predicted = torch.max(outputs.data, 1)  # Получаем индексы максимальных значений
        all_preds.extend(predicted.cpu().numpy())
        all_labels.extend(batch_y.view(-1).cpu().numpy())

# Вычисляем точность
accuracy = 100 * sum(p == l for p, l in zip(all_preds, all_labels)) / len(all_labels)

# Вычисляем F1-меру
f1 = f1_score(all_labels, all_preds, average='weighted') * 100


In [ ]:
metrics = pd.DataFrame({
    "LSTM": [round(accuracy, 3), round(f1, 3), round(loss.item(), 3)],
    },
    index = ["Accuracy", "F1 score", "Loss"])
metrics

LSTM
Accuracy  90.191
F1 score  90.290
Loss       0.165

In [ ]:
def generate_text(model, start_char, length):
    model.eval()

    # Преобразуем начальный символ в последовательность индексов
    input_seq = torch.tensor([char_to_ind[char] for char in start_char], dtype=torch.long).unsqueeze(0)
    generated = start_char

    with torch.no_grad():
        for _ in range(length):
            output = model(input_seq)
            _, predicted_idx = torch.max(output, 1)
            predicted_char = ind_to_char[predicted_idx.item()]
            generated += predicted_char

            # Обновляем input_seq, добавляя новый предсказанный символ
            input_seq = torch.cat((input_seq, torch.tensor([[predicted_idx]], dtype=torch.long)), dim=1)
            input_seq = input_seq[:, -len(start_char):]  # Обрезаем до длины начального символа

    return generated

# Пример генерации текста
generated_text = generate_text(model, 'truth is a', 10)
print("Сгенерированный текст:", generated_text)

Сгенерированный текст: truth is auhzhzuuuuh


### Задание 3

Повторить задание 2 на датасете dostoevsky.txt

Прочитем данные из файла и обработаем их с помощью функции `clean_text`, которая была создана выше.

In [22]:
with open("/content/dostoevsky.txt", 'r', encoding='utf-8') as f:
    text_dst = f.read()

In [23]:
text_dst = clean_text(text_dst)

In [24]:
text_dst = text_dst[:10000]

In [25]:
text_dst[0:10]

' федор мих'

In [26]:
# Кодировка символов числами:

# Объединяем все предложения вместе и извлекаем уникальные символы из объединенных предложений
words = set(text_dst.split())

word_to_idx = {word: idx for idx, word in enumerate(words)}

idx_to_word = {idx: word for word, idx in word_to_idx.items()}

In [27]:
# Подготовка входных и выходных последовательностей
def create_sequences(text, seq_length):
    words = text.split()  # Токенизация
    sequences = []
    next_words = []

    for i in range(len(words) - seq_length):
        sequences.append(words[i:i + seq_length])  # Входная последовательность
        next_words.append(words[i + seq_length])   # Выходное слово

    return sequences, next_words

seq_length = 3
input_seq, target_seq = create_sequences(text_dst, seq_length)

print("Входные последовательности:", input_seq)
print("Выходные слова:", target_seq)

Входные последовательности: [['федор', 'михайлович', 'достоевский'], ['михайлович', 'достоевский', 'бедные'], ['достоевский', 'бедные', 'люди'], ['бедные', 'люди', 'ох'], ['люди', 'ох', 'уж'], ['ох', 'уж', 'эти'], ['уж', 'эти', 'мне'], ['эти', 'мне', 'сказочники'], ['мне', 'сказочники', 'нет'], ['сказочники', 'нет', 'чтобы'], ['нет', 'чтобы', 'написать'], ['чтобы', 'написать', 'что'], ['написать', 'что', 'нибудь'], ['что', 'нибудь', 'полезное'], ['нибудь', 'полезное', 'приятное'], ['полезное', 'приятное', 'усладительное'], ['приятное', 'усладительное', 'а'], ['усладительное', 'а', 'то'], ['а', 'то', 'всю'], ['то', 'всю', 'подноготную'], ['всю', 'подноготную', 'в'], ['подноготную', 'в', 'земле'], ['в', 'земле', 'вырывают'], ['земле', 'вырывают', 'вот'], ['вырывают', 'вот', 'уж'], ['вот', 'уж', 'запретил'], ['уж', 'запретил', 'бы'], ['запретил', 'бы', 'им'], ['бы', 'им', 'писать'], ['им', 'писать', 'ну'], ['писать', 'ну', 'на'], ['ну', 'на', 'что'], ['на', 'что', 'это'], ['что', 'это', '

In [28]:
# Преобразование входных последовательностей в индексы
input_indices = [[word_to_idx[word] for word in seq] for seq in input_seq]
target_indices = [word_to_idx[word] for word in target_seq]

# Преобразование индексов в тензоры
input_tensor = torch.tensor(input_indices)
target_tensor = torch.tensor(target_indices)

print("Входные тензоры:", input_tensor)
print("Выходные тензоры:", target_tensor)

# Проверка размеров тензоров
print("Размер X:", input_tensor.shape)
print("Размер y:", target_tensor.shape)

Входные тензоры: tensor([[390, 457, 685],
        [457, 685, 590],
        [685, 590, 568],
        ...,
        [635, 662, 111],
        [662, 111, 351],
        [111, 351, 702]])
Выходные тензоры: tensor([590, 568, 128,  ..., 351, 702,  62])
Размер X: torch.Size([1672, 3])
Размер y: torch.Size([1672])


In [ ]:
# # Преобразование в индексы
# input_indices = [char_to_ind[symbol] for word in input_seq for symbol in word]
# target_indices = [char_to_ind[word] for word in target_seq if word in char_to_ind]

# # Преобразование списков в тензоры
# input_tensors = [torch.tensor(seq, dtype=torch.long) for seq in input_indices]
# target_tensors = [torch.tensor(seq, dtype=torch.long) for seq in target_indices]

# # Паддинг последовательностей до одинаковой длины
# X_tensor = pad_sequence(input_tensors, batch_first=True)  # Паддинг с добавлением размерности
# y_tensor = pad_sequence(target_tensors, batch_first=True)
# y_tensor = y_tensor[:, 0].unsqueeze(1)

# # Проверка размеров тензоров
# print("Размер X:", X_tensor.shape)
# print("Размер y:", y_tensor.shape)

# # Убедитесь, что размеры не равны (0, 0)
# if X_tensor.size(1) == 0 or y_tensor.size(1) == 0:
#     raise ValueError("Размеры X_tensor или y_tensor равны 0. Проверьте входные данные.")


In [30]:
class LSTMModel(nn.Module):
    def __init__(self, input_size, embedding_dim, hidden_size, output_size):
        super(LSTMModel, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(num_embeddings=input_size, embedding_dim=input_size)

        # Определение LSTM слоя
        self.lstm = nn.LSTM(input_size, hidden_size, batch_first=True)

        # Полносвязный слой для перехода от скрытого состояния к выходу
        self.fc = nn.Linear(hidden_size, output_size)

    def forward(self, x):
      x = self.embedding(x)  # x теперь имеет размер [batch_size, seq_length, embedding_dim]

      # Прямой проход через LSTM
      out, (hn, cn) = self.lstm(x)  # out имеет размер [batch_size, seq_length, hidden_size]


      # Получаем последний временной шаг
      out = out[:, -1, :]  # Теперь out имеет размер [batch_size, hidden_size]

      # Применяем полносвязный слой
      out = self.fc(out)


      return out

In [32]:
input_size = len(words)
embedding_dim = 128
hidden_size = 128
output_size = len(words)


# Предположим, что вы уже создали экземпляр вашей модели
model_dst = LSTMModel(input_size, embedding_dim, hidden_size, output_size)


# Определение функции потерь и оптимизатора
criterion = nn.CrossEntropyLoss()  # Для многоклассовой классификации
optimizer = optim.Adam(model_dst.parameters(), lr=0.001)

In [33]:
model_dst

LSTMModel(
  (embedding): Embedding(767, 767)
  (lstm): LSTM(767, 128, batch_first=True)
  (fc): Linear(in_features=128, out_features=767, bias=True)
)

In [34]:
# Создание TensorDataset
dataset = TensorDataset(input_tensor, target_tensor)

# Создание DataLoader
dataloader = DataLoader(dataset, batch_size=128)

In [39]:
# Пример цикла обучения
num_epochs = 50
for epoch in range(num_epochs):
    model_dst.train()
    for batch_X, batch_y in dataloader:
        optimizer.zero_grad()
        outputs = model_dst(batch_X)

        batch_y = batch_y.view(-1)

        # Проверяем, что batch_y содержит индексы классов
        loss = criterion(outputs, batch_y)
        loss.backward()
        optimizer.step()

    print(f'Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}')

Epoch [1/50], Loss: 0.3291
Epoch [2/50], Loss: 0.2671
Epoch [3/50], Loss: 0.2254
Epoch [4/50], Loss: 0.1899
Epoch [5/50], Loss: 0.1632
Epoch [6/50], Loss: 0.1414
Epoch [7/50], Loss: 0.1248
Epoch [8/50], Loss: 0.1096
Epoch [9/50], Loss: 0.0987
Epoch [10/50], Loss: 0.0891
Epoch [11/50], Loss: 0.0812
Epoch [12/50], Loss: 0.0736
Epoch [13/50], Loss: 0.0672
Epoch [14/50], Loss: 0.0616
Epoch [15/50], Loss: 0.0568
Epoch [16/50], Loss: 0.0524
Epoch [17/50], Loss: 0.0484
Epoch [18/50], Loss: 0.0448
Epoch [19/50], Loss: 0.0417
Epoch [20/50], Loss: 0.0388
Epoch [21/50], Loss: 0.0362
Epoch [22/50], Loss: 0.0340
Epoch [23/50], Loss: 0.0319
Epoch [24/50], Loss: 0.0301
Epoch [25/50], Loss: 0.0283
Epoch [26/50], Loss: 0.0267
Epoch [27/50], Loss: 0.0252
Epoch [28/50], Loss: 0.0239
Epoch [29/50], Loss: 0.0226
Epoch [30/50], Loss: 0.0215
Epoch [31/50], Loss: 0.0204
Epoch [32/50], Loss: 0.0194
Epoch [33/50], Loss: 0.0185
Epoch [34/50], Loss: 0.0177
Epoch [35/50], Loss: 0.0169
Epoch [36/50], Loss: 0.0162
E

In [40]:
model_dst.eval()  # Переключаем модель в режим оценки
all_preds = []
all_labels = []
with torch.no_grad():
    for batch_X, batch_y in dataloader:
        outputs = model_dst(batch_X)
        _, predicted = torch.max(outputs.data, 1)  # Получаем индексы максимальных значений
        all_preds.extend(predicted.cpu().numpy())
        all_labels.extend(batch_y.view(-1).cpu().numpy())

# Вычисляем точность
accuracy_dst = 100 * sum(p == l for p, l in zip(all_preds, all_labels)) / len(all_labels)

# Вычисляем F1-меру
f1_dst = f1_score(all_labels, all_preds, average='weighted') * 100


In [41]:
metrics = pd.DataFrame({
    "LSTM": [round(accuracy_dst, 3), round(f1_dst, 3), round(loss.item(), 3)],
    },
    index = ["Accuracy", "F1 score", "Loss"])
metrics

LSTM
Accuracy  99.222
F1 score  99.079
Loss       0.010

In [60]:
def generate_text(model, start_char, length):
    model.eval()

    # Преобразуем начальный символ в последовательность индексов
    input_seq = torch.tensor([char_to_ind[char] for char in start_char], dtype=torch.long).unsqueeze(0)
    generated = start_char

    with torch.no_grad():
        for _ in range(length):
            output = model(input_seq)
            _, predicted_idx = torch.max(output, 1)
            predicted_char = idx_to_word[predicted_idx.item()]
            generated += predicted_char + " "

            # Обновляем input_seq, добавляя новый предсказанный символ
            input_seq = torch.cat((input_seq, torch.tensor([[predicted_idx]], dtype=torch.long)), dim=1)
            input_seq = input_seq[:, -len(start_char):]  # Обрезаем до длины начального символа

    return generated

# Пример генерации текста
generated_text = generate_text(model_dst, 'бог', 10)
print("Сгенерированный текст:", generated_text)

Сгенерированный текст: боги о брамбеусе и о разных у них там сочинителях 


In [58]:
def generate_text(model, start_char, length):
    model.eval()

    # Преобразуем начальный символ в последовательность индексов
    input_seq = torch.tensor([word_to_idx[char] for char in start_char.split(" ") if char in word_to_idx], dtype=torch.long).unsqueeze(0)
    generated = start_char

    with torch.no_grad():
        for _ in range(length):
            output = model(input_seq)
            _, predicted_idx = torch.max(output, 1)
            predicted_char = idx_to_word[predicted_idx.item()]
            generated += predicted_char + " "

            # Обновляем input_seq, добавляя новый предсказанный символ
            input_seq = torch.cat((input_seq, torch.tensor([[predicted_idx]], dtype=torch.long)), dim=1)
            input_seq = input_seq[:, -len(start_char):]  # Обрезаем до длины начального символа

    return generated

# Пример генерации текста
generated_text = generate_text(model_dst, 'бог ', 10)
print("Сгенерированный текст:", generated_text)

Сгенерированный текст: бог с ними а вот куда это вы утром ходили сегодня 
